In [112]:
import pandas as pd


# datapath = '/Users/alex/project/MIMO/data/notxbf_com_excels_f4/341c-f0d4-70be/train/341c-f0d4-70be_0.xlsx'
# datapath = '/Users/alex/project/MIMO/data/notxbf_com_excels_f4/bc98-2983-907b/train/bc98-2983-907b_0.xlsx'
# datapath = '/Users/alex/project/MIMO/data/notxbf_com_excels_f4/d0c1-bfe4-18f0/train/d0c1-bfe4-18f0_0.xlsx'

# 问题3
datapath = '/Users/alex/project/MIMO/data/txbf_com_excels_f4/fc02-9668-e2fd/train/fc02-9668-e2fd_0.xlsx'
df = pd.DataFrame(pd.read_excel(datapath))





In [72]:
import re
import numpy as np

In [113]:
def extract_to_list(s):
    pattern = r'([-+]?\d*\.?\d+(?:e[-+]?\d+)?[+-]\d*\.?\d+(?:e[-+]?\d+)?j|[-+]?\d*\.?\d+(?:e[-+]?\d+)?j)'
    matches = re.findall(pattern, s)
    result = []
    for m in matches:
        m.strip()
        result.append(complex(m.replace(' ', '')))
    return result

def row_to_matrix(row, i):
    H = np.zeros((2, 4), dtype=complex)
    
    for r in range(2):
        for c in range(4):
            try:
                H[r, c] = row[f'csi_matrix_r{r}_c{c}'][i]
            except Exception as e:
                print(row[f'csi_matrix_r{r}_c{c}'][i])
                print(type(row[f'csi_matrix_r{r}_c{c}'][i]))
                print(f"Error at row {i}, r{r}, c{c}: {e}")
                raise ValueError(f" at row {i}, r{r}, c{c}")

    noise = 10 ** ((row['noise_floor'] - 30) / 10) 
    gain = np.linalg.norm(H, 'fro') ** 2
    sinr = gain / noise

    U, S, Vh = np.linalg.svd(H,full_matrices=True)
    V = Vh.conj().T
    H_proj = H @ V
    H_proj = np.abs(H_proj) / noise



    # H = (np.abs(H))/noise 
    return pd.Series([sinr, H_proj])

def to_matrix(df):
    csi_matrix = ['csi_matrix_r0_c0', 'csi_matrix_r0_c1',
       'csi_matrix_r0_c2', 'csi_matrix_r0_c3', 'csi_matrix_r1_c0',
       'csi_matrix_r1_c1', 'csi_matrix_r1_c2', 'csi_matrix_r1_c3']


    for col in csi_matrix:
        df[col] = df[col].apply(extract_to_list)

    for i in range(122):
        df[[f'sinr_{i+1}', f'H_{i+1}']] = df.apply(lambda row: row_to_matrix(row, i), axis=1)
    return df

df = to_matrix(df)


/var/folders/j5/z650dsh51j7ct9mcy_pkwzkm0000gn/T/ipykernel_49496/2614754194.py:47: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[[f'sinr_{i+1}', f'H_{i+1}']] = df.apply(lambda row: row_to_matrix(row, i), axis=1)
/var/folders/j5/z650dsh51j7ct9mcy_pkwzkm0000gn/T/ipykernel_49496/2614754194.py:47: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[[f'sinr_{i+1}', f'H_{i+1}']] = df.apply(lambda row: row_to_matrix(row, i), axis=1)
/var/folders/j5/z650dsh51j7ct9mcy_pkwzkm0000gn/T/ipykernel_49496/2614754194.py:47: PerformanceWarning: D

In [74]:
df

Unnamed: 0                                   csi_matrix_r0_c0  \
0              0  [(-3.154906390107002e-05+3.7896773454738764e-0...   
1              1  [(2.4285854441085734e-05+4.229247655519874e-05...   
2              2  [(-4.2008097505065764e-05-2.1096171773377327e-...   
3              3  [(-4.097164312615073e-05-1.8887636902126217e-0...   
4              4  [(-6.412022249499807e-06-4.6363853188690904e-0...   
...          ...                                                ...   
5029        5029  [(-1.5771913016369872e-06-6.61402803912285e-07...   
5030        5030  [(-2.476904447203785e-06-6.059379978138015e-07...   
5031        5031  [(-1.7306594494301278e-06-2.1082578747603375e-...   
5032        5032  [(-5.258310583126221e-07+2.5656929224564146e-0...   
5033        5033  [(-1.2898142322492935e-06+2.9363855925675407e-...   

                                       csi_matrix_r0_c1  \
0     [(-7.074064378217903e-06-1.6106128718263976e-0...   
1     [(-4.0322521315364146e-06+8.618554174276307e-0...   
2     [(-1.2651561529303434e-05-2.947936667022159e-0...   
3     [(-8.555938083869141e-06-1.937193528423202e-06...   
4     [(-4.294023949891274e-06-7.282432509612903e-06...   
...                                                 ...   
5029  [(-6.4613966228354e-06-1.7705244289344244e-06j...   
5030  [(-1.0609230207336383e-05-2.476904447203785e-0...   
5031  [(-8.674274937446762e-06-6.3877066951693804e-0...   
5032  [(-1.5140308058311706e-06+1.1133112751860344e-...   
5033  [(-3.823704603405707e-06+1.0611237655384259e-0...   

                                       csi_matrix_r0_c2  \
0     [(-2.3938128565576656e-05-1.853783834827638e-0...   
1     [(-2.3085412966811535e-05+1.8622233126561308e-...   
2     [(-1.136183923748124e-06-3.16596114968734e-05j...   
3     [(-2.9380768514418563e-06-3.2125126013018096e-...   
4     [(2.828833345367562e-05-1.7466232552936125e-05...   
...                                                 ...   
5029  [(-3.90736425695873e-06-7.66209709763001e-06j)...   
5030  [(-7.175581553058175e-06-1.1523452449651944e-0...   
5031  [(-1.9614140426874785e-06-1.3247411422001524e-...   
5032  [(-1.0362498269850468e-05+8.25010798387045e-06...   
5033  [(-1.180042808228077e-05+5.323914065028999e-06...   

                                       csi_matrix_r0_c3  \
0     [(7.579354690947754e-06+2.3274935030118725e-05...   
1     [(2.545551536473752e-05+1.8160524867225075e-06...   
2     [(-1.572232889078485e-05+1.9253711356488475e-0...   
3     [(-1.8532484755248632e-05+2.243915837090209e-0...   
4     [(-2.393628215311014e-05-7.717637639669451e-06...   
...                                                 ...   
5029  [(2.309822099816749e-06-5.667713258140657e-06j...   
5030  [(3.2848217776221868e-06-8.929612599361285e-06...   
5031  [(6.880682417128265e-06-7.058992784645308e-06j...   
5032  [(-9.301770100495695e-06-2.221182918734352e-06...   
5033  [(-8.644499641670797e-06-4.4914807662014405e-0...   

                                       csi_matrix_r1_c0  \
0     [(-5.0115317767327056e-05+1.4368727471751114e-...   
1     [(2.158352352463146e-05+4.830598122179422e-05j...   
2     [(-4.6237633866686486e-05-2.1914711884731614e-...   
3     [(-5.2435315056106985e-05-1.073675498767905e-0...   
4     [(-1.3349637756377608e-05-5.161065311170986e-0...   
...                                                 ...   
5029  [(2.062416198322095e-06+5.351133919970841e-06j...   
5030  [(-2.955741920274741e-06+7.494917012125237e-06...   
5031  [(-6.074231189553656e-07+7.106850491777777e-06...   
5032  [(6.145011759591898e-06-4.8091396379414855e-06...   
5033  [(9.542746964564884e-06+7.068701455233247e-07j...   

                                       csi_matrix_r1_c1  \
0     [(8.06050565488477e-06+2.277968989423957e-06j)...   
1     [(8.564890287552167e-07-3.939849532273997e-06j...   
2     [(-2.528620602084417e-06+1.7098291690285107e-0...   
3     [(-6.242299411441309e-07+1.4232442658086183e-0...   
4     [(-1.18001262310

In [114]:
H_columns = [f'H_{i+1}' for i in range(122)]
other_columns = ['Unnamed: 0', 'mcs',
    'dfx_time', 'csi_time', 'beamforming_en', 'noise_floor',
]

df_to_save = df[H_columns + other_columns]
df_to_save.to_pickle(datapath.replace('.xlsx', '_H.pkl'))

# valid

In [116]:
import pandas as pd
import re
import numpy as np


# infer_datapath = '/Users/alex/project/MIMO/data/notxbf_com_excels_f4/341c-f0d4-70be/valid/341c-f0d4-70be_0.xlsx'
# infer_datapath = '/Users/alex/project/MIMO/data/notxbf_com_excels_f4/bc98-2983-907b/valid/bc98-2983-907b_0.xlsx'
# infer_datapath = '/Users/alex/project/MIMO/data/notxbf_com_excels_f4/d0c1-bfe4-18f0/valid/d0c1-bfe4-18f0_0.xlsx'

infer_datapath = '/Users/alex/project/MIMO/data/txbf_com_excels_f4/fc02-9668-e2fd/valid/fc02-9668-e2fd_0.xlsx'

infer_df = pd.DataFrame(pd.read_excel(infer_datapath))

In [117]:
def extract_to_list(s):
    pattern = r'([-+]?\d*\.?\d+(?:e[-+]?\d+)?[+-]\d*\.?\d+(?:e[-+]?\d+)?j|[-+]?\d*\.?\d+(?:e[-+]?\d+)?j)'
    matches = re.findall(pattern, s)
    result = []
    for m in matches:
        m.strip()
        result.append(complex(m.replace(' ', '')))
    return result

def row_to_matrix(row, i):
    H = np.zeros((2, 4), dtype=complex)
    
    for r in range(2):
        for c in range(4):
            try:
                H[r, c] = row[f'csi_matrix_r{r}_c{c}'][i]
            except Exception as e:
                print(row[f'csi_matrix_r{r}_c{c}'][i])
                print(type(row[f'csi_matrix_r{r}_c{c}'][i]))
                print(f"Error at row {i}, r{r}, c{c}: {e}")
                raise ValueError(f" at row {i}, r{r}, c{c}")

    noise = 10 ** ((row['noise_floor'] - 30) / 10) 
    gain = np.linalg.norm(H, 'fro') ** 2
    sinr = gain / noise
    U, S, Vh = np.linalg.svd(H,full_matrices=True)
    V = Vh.conj().T
    H_proj = H @ V
    H_proj = np.abs(H_proj) / noise



    # H = (np.abs(H))/noise 
    return pd.Series([sinr, H_proj])

def to_matrix(df):
    csi_matrix = ['csi_matrix_r0_c0', 'csi_matrix_r0_c1',
       'csi_matrix_r0_c2', 'csi_matrix_r0_c3', 'csi_matrix_r1_c0',
       'csi_matrix_r1_c1', 'csi_matrix_r1_c2', 'csi_matrix_r1_c3']


    for col in csi_matrix:
        df[col] = df[col].apply(extract_to_list)

    for i in range(122):
        df[[f'sinr_{i+1}', f'H_{i+1}']] = df.apply(lambda row: row_to_matrix(row, i), axis=1)
    return df

infer_df = to_matrix(infer_df)


/var/folders/j5/z650dsh51j7ct9mcy_pkwzkm0000gn/T/ipykernel_49496/1401798762.py:46: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[[f'sinr_{i+1}', f'H_{i+1}']] = df.apply(lambda row: row_to_matrix(row, i), axis=1)
/var/folders/j5/z650dsh51j7ct9mcy_pkwzkm0000gn/T/ipykernel_49496/1401798762.py:46: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[[f'sinr_{i+1}', f'H_{i+1}']] = df.apply(lambda row: row_to_matrix(row, i), axis=1)
/var/folders/j5/z650dsh51j7ct9mcy_pkwzkm0000gn/T/ipykernel_49496/1401798762.py:46: PerformanceWarning: D

In [78]:
infer_df

Unnamed: 0                                   csi_matrix_r0_c0  \
0              0  [(-8.714614499978461e-07+2.7866499854582292e-0...   
1              1  [(-5.309270364919181e-07+2.8874979177630635e-0...   
2              2  [(-2.924120462196956e-06-2.7413629333096467e-0...   
3              3  [(1.2330525006384934e-06+2.5463035379038804e-0...   
4              4  [(-2.7827024404378335e-06+9.686622419245623e-0...   
...          ...                                                ...   
5029        5029  [(3.855663331799695e-06+1.3169549651826119e-06...   
5030        5030  [(2.8850997033926468e-06+5.718215628345786e-07...   
5031        5031  [(2.7840311154371307e-06-5.487753641005883e-06...   
5032        5032  [(-4.72644978477001e-06-1.1333833667560737e-06...   
5033        5033  [(3.405578086013183e-06-5.367191063556776e-06j...   

                                       csi_matrix_r0_c1  \
0     [(-1.975988171506744e-06+1.087300157962429e-05...   
1     [(-5.402415459040571e-07+1.0860717974553977e-0...   
2     [(-1.0762387812252685e-05-1.1676175456689236e-...   
3     [(6.686552991267277e-06+9.453402504895115e-06j...   
4     [(-1.1139615782132467e-05-1.2680669348830633e-...   
...                                                 ...   
5029  [(1.4438903835134662e-05+1.2233400941636072e-0...   
5030  [(1.0929589416906379e-05+1.0149832740313772e-0...   
5031  [(2.1656549734506144e-05-1.9006366268849645e-0...   
5032  [(-2.409042517849612e-05-1.5674450816839316e-0...   
5033  [(1.953439590137162e-05-2.2013656747989217e-05...   

                                       csi_matrix_r0_c2  \
0     [(-1.0538603581369303e-05+7.589821233120777e-0...   
1     [(-9.593944694503083e-06+8.783582375646997e-06...   
2     [(-8.67082942609792e-06-1.0214115225590758e-05...   
3     [(-2.8670976844114557e-06+1.2821741043224659e-...   
4     [(-8.41855548436256e-06-1.0012445173347521e-05...   
...                                                 ...   
5029  [(-1.792962783923315e-05+1.8246966385060287e-0...   
5030  [(-1.4854364689089166e-05+7.667607319827305e-0...   
5031  [(-2.114792866533974e-06+2.9500022011651137e-0...   
5032  [(2.852750048664756e-05-6.221551247299299e-06j...   
5033  [(2.8879302169391794e-06+2.9233482290337166e-0...   

                                       csi_matrix_r0_c3  \
0     [(-9.606342495325096e-06-2.8981159848765578e-0...   
1     [(-1.0003783108637196e-05-1.965361485961311e-0...   
2     [(2.2641627189927823e-06-9.462778717942929e-06...   
3     [(-8.300548540883515e-06+4.0500260996581405e-0...   
4     [(2.0341907080415805e-06-9.554532113528636e-06...   
...                                                 ...   
5029  [(-1.301088037891255e-06+1.7421886165909734e-0...   
5030  [(-1.949391691481518e-06+1.3333839169733584e-0...   
5031  [(2.639475653674049e-05+9.181948774951305e-06j...   
5032  [(9.645815887285734e-07-2.8648073185238632e-05...   
5033  [(2.6972178441224415e-05+5.176478690740038e-06...   

                                       csi_matrix_r1_c0  \
0     [(1.2190104365442231e-05-3.125667786010828e-07...   
1     [(7.385787509530639e-06+1.0071528422087234e-06...   
2     [(3.7175406194841624e-06+7.744876290592005e-06...   
3     [(2.4191193193588224e-06-1.153733829232669e-05...   
4     [(5.18961505504117e-06+9.84421824873789e-06j),...   
...                                                 ...   
5029  [(-2.1944091995106763e-06+1.2351388922960093e-...   
5030  [(1.4553192034211481e-06+9.446808864312717e-06...   
5031  [(1.9995735787375436e-05+4.1699650008848275e-0...   
5032  [(-8.935520200760335e-06-1.8200243777338155e-0...   
5033  [(1.860621219994697e-05-5.437204101324986e-06j...   

                                       csi_matrix_r1_c1  \
0     [(-6.928563592324002e-06-9.741664599733747e-06...   
1     [(-8.434905053498059e-06-1.2589410527609043e-0...   
2     [(8.984056497086725e-06-9.293851548710407e-06j...   
3     [(-1.246776879977239e-05+9.92459207942081e-07j...   
4     [(4.601102007562

In [118]:
H_columns = [f'H_{i+1}' for i in range(122)]
other_columns = ['Unnamed: 0',
    'dfx_time', 'csi_time', 'beamforming_en', 'noise_floor',
]

df_to_save = infer_df[H_columns + other_columns]
df_to_save.to_pickle(infer_datapath.replace('.xlsx', '_H.pkl'))

In [122]:
import os
import numpy as np
import pandas as pd
import matplotlib
matplotlib.use("Agg")
import matplotlib.pyplot as plt
from scipy.stats import gaussian_kde  # 若无需要可去掉

base_dir = "/Users/alex/project/MIMO/data/notxbf_com_excels_f4"
sub_dirs = [
    "341c-f0d4-70be",
    "bc98-2983-907b",
    "d0c1-bfe4-18f0",
]
pkl_suffix = "_0_H.pkl"
H_cols = [f"H_{i+1}" for i in range(122)]
out_dir = "./H_stats_result"
os.makedirs(out_dir, exist_ok=True)

all_stats = []

def collect_H_values(df):
    mats = []
    for col in H_cols:
        arr = np.vstack(df[col].apply(lambda x: np.array(x).reshape(-1)))
        mats.append(arr)
    big = np.concatenate(mats, axis=1)
    return big.ravel()

for d in sub_dirs:
    pkl_path = os.path.join(base_dir, d, "train", f"{d}{pkl_suffix}")
    if not os.path.isfile(pkl_path):
        print(f"缺失: {pkl_path}")
        continue
    df = pd.read_pickle(pkl_path)
    vals = collect_H_values(df).astype(float)

    stats = {
        "dataset": d,
        "count": vals.size,
        "mean":  vals.mean(),
        "std":   vals.std(),
        "min":   vals.min(),
        "p01":   np.percentile(vals, 1),
        "p25":   np.percentile(vals, 25),
        "median":np.percentile(vals, 50),
        "p75":   np.percentile(vals, 75),
        "p99":   np.percentile(vals, 99),
        "max":   vals.max()
    }
    all_stats.append(stats)

    plt.figure(figsize=(5,4), dpi=150)
    # 经验分布直方图
    plt.hist(vals, bins=120, density=True, alpha=0.55, color="#1f77b4", edgecolor='none', label="Histogram(PDF)")
    # 可选：核密度
    try:
        kde = gaussian_kde(vals)
        xs = np.linspace(vals.min(), vals.max(), 400)
        plt.plot(xs, kde(xs), color="red", lw=1.2, label="KDE")
    except Exception as e:
        print(f"KDE fail {d}: {e}")

    plt.xlabel("H value")
    plt.ylabel("Density")
    plt.title(f"PDF of H entries - {d}")
    plt.grid(alpha=0.3, linestyle='--', linewidth=0.4)
    plt.legend()
    plt.tight_layout()
    plt.savefig(os.path.join(out_dir, f"{d}_H_PDF.pdf"))
    plt.close()

# 统计表
pd.DataFrame(all_stats).to_excel(os.path.join(out_dir, "H_global_stats.xlsx"), index=False)
print("Done. 输出目录:", out_dir)

Done. 输出目录: ./H_stats_result
